In [1]:
import os
import pandas as pd
import tensorflow as tf
import numpy as np

In [167]:
data=pd.read_csv('train.csv')
data.head(5)

id                                       comment_text  toxic  \
0  0000997932d777bf  Explanation\nWhy the edits made under my usern...      0   
1  000103f0d9cfb60f  D'aww! He matches this background colour I'm s...      0   
2  000113f07ec002fd  Hey man, I'm really not trying to edit war. It...      0   
3  0001b41b1c6bb37e  "\nMore\nI can't make any real suggestions on ...      0   
4  0001d958c54c6e35  You, sir, are my hero. Any chance you remember...      0   

   severe_toxic  obscene  threat  insult  identity_hate  
0             0        0       0       0              0  
1             0        0       0       0              0  
2             0        0       0       0              0  
3             0        0       0       0              0  
4             0        0       0       0              0

1/1 [==============================] - 0s 327ms/step


In [4]:
data['comment_text'][8]

"Sorry if the word 'nonsense' was offensive to you. Anyway, I'm not intending to write anything in the article(wow they would jump on me for vandalism), I'm merely requesting that it be more encyclopedic so one can use it for school as a reference. I have been to the selective breeding page but it's almost a stub. It points to 'animal breeding' which is a short messy article that gives you no info. There must be someone around with expertise in eugenics? 93.161.107.169"

In [5]:
 data.columns

Index(['id', 'comment_text', 'toxic', 'severe_toxic', 'obscene', 'threat',
       'insult', 'identity_hate'],
      dtype='object')

In [6]:
data.shape

(159571, 8)

In [7]:
data[data.columns[2:]].iloc[9]

toxic            0
severe_toxic     0
obscene          0
threat           0
insult           0
identity_hate    0
Name: 9, dtype: int64

## Preprocessing

In [8]:
from tensorflow.keras.layers import TextVectorization

In [9]:
x=data['comment_text']
y=data[data.columns[2:]].values

In [10]:
x

0         Explanation\nWhy the edits made under my usern...
1         D'aww! He matches this background colour I'm s...
2         Hey man, I'm really not trying to edit war. It...
3         "\nMore\nI can't make any real suggestions on ...
4         You, sir, are my hero. Any chance you remember...
                                ...                        
159566    ":::::And for the second time of asking, when ...
159567    You should be ashamed of yourself \n\nThat is ...
159568    Spitzer \n\nUmm, theres no actual article for ...
159569    And it looks like it was actually you who put ...
159570    "\nAnd ... I really don't think you understand...
Name: comment_text, Length: 159571, dtype: object

In [11]:
y

array([[0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       ...,
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0]], dtype=int64)

In [12]:
max_features=200000

In [13]:
vectorizer=TextVectorization(max_tokens=max_features,
                            output_sequence_length=1800,
                            output_mode='int')

In [14]:
vectorizer.get_vocabulary()

['', '[UNK]']

In [15]:
vectorizer.adapt(x.values)

In [16]:
vectorizer("have you watched breaking bad")[:5]

<tf.Tensor: shape=(5,), dtype=int64, numpy=array([  19,    7, 3666, 2891,  338], dtype=int64)>

In [17]:
vectorized_text=vectorizer(x.values)

In [18]:
vectorized_text

<tf.Tensor: shape=(159571, 1800), dtype=int64, numpy=
array([[  645,    76,     2, ...,     0,     0,     0],
       [    1,    54,  2489, ...,     0,     0,     0],
       [  425,   441,    70, ...,     0,     0,     0],
       ...,
       [32445,  7392,   383, ...,     0,     0,     0],
       [    5,    12,   534, ...,     0,     0,     0],
       [    5,     8,   130, ...,     0,     0,     0]], dtype=int64)>

In [19]:
dataset=tf.data.Dataset.from_tensor_slices((vectorized_text, y))
dataset=dataset.cache()
dataset=dataset.shuffle(160000)
dataset=dataset.batch(16)
dataset=dataset.prefetch(8)

In [20]:
159571/16

9973.1875

In [21]:
batch_x, batch_y = dataset.as_numpy_iterator().next()

In [22]:
batch_x.shape

(16, 1800)

In [23]:
batch_y.shape

(16, 6)

In [24]:
len(dataset)

9974

In [25]:
int(len(dataset)*.7)

6981

In [26]:
train=dataset.take(int(len(dataset)*.7))
val=dataset.skip(int(len(dataset)*.7)).take(int(len(dataset)*.2))
test=dataset.skip(int(len(dataset)*.9)).take(int(len(dataset)*.1))

In [27]:
len(train),len(val),len(test)

(6981, 1994, 997)

In [28]:
train_generator=train.as_numpy_iterator()

In [29]:
train_generator.next()

(array([[    73,      9,     12, ...,      0,      0,      0],
        [182862,     88,      7, ...,      0,      0,      0],
        [  4384,    274,    139, ...,      0,      0,      0],
        ...,
        [    14,      9,     21, ...,      0,      0,      0],
        [  1188,    399,    123, ...,      0,      0,      0],
        [ 46927,    175,    425, ...,      0,      0,      0]], dtype=int64),
 array([[0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [1, 0, 1, 0, 1, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0]], dtype=int64))

In [30]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dropout, Bidirectional, Dense, Embedding

In [31]:
model=Sequential()

In [32]:
model.add(Embedding(max_features+1, 32))
model.add(Bidirectional(LSTM(32, activation='tanh')))
model.add(Dense(128, activation='relu'))
model.add(Dense(256, activation='relu'))
model.add(Dense(128, activation='relu'))
model.add(Dense(6, activation='sigmoid'))

In [33]:
model.compile(loss='BinaryCrossentropy', optimizer='adam', metrics=['accuracy'])

In [34]:
model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding (Embedding)       (None, None, 32)          6400032   
                                                                 
 bidirectional (Bidirection  (None, 64)                16640     
 al)                                                             
                                                                 
 dense (Dense)               (None, 128)               8320      
                                                                 
 dense_1 (Dense)             (None, 256)               33024     
                                                                 
 dense_2 (Dense)             (None, 128)               32896     
                                                                 
 dense_3 (Dense)             (None, 6)                 774       
                                                        

In [36]:
history=model.fit(train, epochs=10, validation_data=val)

Epoch 1/10

6981/6981 [==============================] - 5071s 726ms/step - loss: 0.0635 - accuracy: 0.9855 - val_loss: 0.0452 - val_accuracy: 0.9946
Epoch 2/10
6981/6981 [==============================] - 4516s 647ms/step - loss: 0.0454 - accuracy: 0.9942 - val_loss: 0.0399 - val_accuracy: 0.9938
Epoch 3/10
6981/6981 [==============================] - 4100s 587ms/step - loss: 0.0407 - accuracy: 0.9889 - val_loss: 0.0373 - val_accuracy: 0.9941
Epoch 4/10
6981/6981 [==============================] - 4111s 589ms/step - loss: 0.0371 - accuracy: 0.9920 - val_loss: 0.0327 - val_accuracy: 0.9948
Epoch 5/10
6981/6981 [==============================] - 4691s 672ms/step - loss: 0.0334 - accuracy: 0.9941 - val_loss: 0.0302 - val_accuracy: 0.9940
Epoch 6/10
6981/6981 [==============================] - 5055s 724ms/step - loss: 0.0311 - accuracy: 0.9841 - val_loss: 0.0275 - val_accuracy: 0.9944
Epoch 7/10
6981/6981 [==============================] - 4508s 646ms/step - loss: 0.0277 - accuracy: 0.993

In [37]:
model.evaluate(test)

997/997 [==============================] - 158s 146ms/step - loss: 0.0188 - accuracy: 0.9940


[0.018809018656611443, 0.9939819574356079]

In [40]:
x_batch, y_batch = test.as_numpy_iterator().next()

In [41]:
(model.predict(x_batch) > 0.5).astype(int)

1/1 [==============================] - 2s 2s/step


array([[0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [1, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [1, 0, 1, 0, 1, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0]])

In [42]:
y_batch

array([[0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [1, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [1, 0, 1, 0, 1, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0]], dtype=int64)

In [49]:
input_text=vectorizer('I am coming to kill you pal')

In [50]:
input_text[:7]

<tf.Tensor: shape=(7,), dtype=int64, numpy=array([   8,   74,  939,    3,  950,    7, 5762], dtype=int64)>

In [51]:
batch=test.as_numpy_iterator().next()

In [52]:
res=model.predict(np.expand_dims(input_text,0))

1/1 [==============================] - 0s 78ms/step


In [53]:
data.columns[2:]

Index(['toxic', 'severe_toxic', 'obscene', 'threat', 'insult',
       'identity_hate'],
      dtype='object')

In [54]:
res

array([[0.54140395, 0.00114176, 0.01782109, 0.10045966, 0.0319472 ,
        0.02094165]], dtype=float32)

## Evaluate the Model

In [59]:
model.save('finalproject.keras')

In [60]:
model.save('finalprojecttoxic.h5')

C:\Users\karti\anaconda3\Lib\site-packages\keras\src\engine\training.py:3103: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


## Making a Language Translation

In [97]:
from transformers import pipeline

In [125]:
translator_german=pipeline("translation", model="Helsinki-NLP/opus-mt-de-en", tokenizer="Helsinki-NLP/opus-mt-de-en")

In [120]:
german="Hallo, wie heißt du?"

In [126]:
en_to_german=translator_german(german)
en_to_german[0]['translation_text']

"Hello, what's your name?"

In [107]:
translator_spanish = pipeline("translation", model="Helsinki-NLP/opus-mt-es-en", tokenizer="Helsinki-NLP/opus-mt-es-en")

In [117]:
spanish_text = "hola como estas"

In [124]:
en_to_spanish = translator(spanish_text)
en_to_spanish[0]['translation_text']

'Hello, how are you?'

## Test and Gradio

In [61]:
import gradio as gr

In [62]:
model=tf.keras.models.load_model('finalprojecttoxic.h5')

In [73]:
input_str=vectorizer('Hey i freaking hate you!. I\'m going to hurt you!')

In [74]:
res=model.predict(np.expand_dims(input_str,0))

1/1 [==============================] - 0s 88ms/step


In [75]:
res

array([[0.9133858 , 0.00198671, 0.0333592 , 0.00411558, 0.71037763,
        0.00563182]], dtype=float32)

In [72]:
data.columns[2:]

Index(['toxic', 'severe_toxic', 'obscene', 'threat', 'insult',
       'identity_hate'],
      dtype='object')

In [122]:
translator_hindi = pipeline("translation", model="Helsinki-NLP/opus-mt-hi-en", tokenizer="Helsinki-NLP/opus-mt-hi-en")

In [104]:
hindi_text = "नमस्ते, आप कैसे हैं?"

In [123]:
en_to_hin = translator_hindi(hindi_text)
en_to_hin[0]['translation_text']

'Hello, how are you?'

In [131]:
def translate_hindi(from_text):
    result2 = translator_hindi(from_text)
    
    return result2[0]['translation_text']

In [133]:
translate_hindi('नमस्ते, आप कैसे हैं?')

'Hello, how are you?'

In [94]:
def score_comment(comment):
    vectorized_comment = vectorizer([comment])
    results=model.predict(vectorized_comment)
    
    text=''
    for idx, col in enumerate(data.columns[2:]):
        text+= '{}: {}\n'.format(col, results[0][idx]>0.5)
        
    return text

In [163]:
def combined_models(input):
    output1=translate_hindi(input)
    output2=score_comment(input)
    
    return output1, output2

In [166]:
interface = gr.Interface(fn=combined_models, inputs="text", outputs=["text","text"],title="Toxic Comment Analyzer")

1/1 [==============================] - 0s 109ms/step


In [168]:
interface.launch(share=True)

Running on local URL:  http://127.0.0.1:7871
Running on public URL: https://27f88e54e3177749fa.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)


1/1 [==============================] - 0s 426ms/step
